In [1]:
from langchain_core.documents import Document
import glob
import re

In [2]:
pattern =r'(?=제\s*\d+\s*조(?:의\s*\d+)?\s*\([^)]+\))'
documents=[]
except_documents=[]

for file_path in glob.glob('./datas/*.txt'):
    file_name = file_path.split('/')[-1].replace('.txt', '')
    with open(file_path, 'r', encoding='utf-8') as f:
        text = f.read()
    
    url = text.split('#url#')[-1]
    text = text.split('#url#')[0]

    articles = re.split(pattern, text)
    articles = [c.strip() for c in articles if c.strip()]
    doc = {
        'url': url,
        'articles': articles,
        'title': file_name,
        'source': file_path
    }

    if ('제1조(목적)' in articles[0]) or ('제1조 (목적)' in articles[0]) or ('제1조(취지)' in articles[0]):
        documents.append(doc)
    else:
        except_documents.append(doc)

print(len(documents), len(except_documents))


100 56


In [3]:
delete_list=[]
for i,item in enumerate(except_documents):
    if ('제1장 총칙' in item['articles'][0]) or ('제1편 총칙' in item['articles'][0]):
        item['articles'].pop(0)
        documents.append(item)
        delete_list.append(i)
    else:
        print(item['articles'][0])

for i in sorted(delete_list, reverse=True):
    except_documents.pop(i)

print(len(documents), len(except_documents))


제1조(국내재산의 범위)「국내재산 도피 방지법」(이하 “법”이라 한다)제1조에 따른 재산은 다음 각 호의 어느 하나에 해당하는 것으로 한다.1. 화폐ㆍ보조화폐 및 은행권2. 유가증권 또는 그 밖의 채권3. 금ㆍ은ㆍ백금 또는 그 밖의 귀금속 및 보석류4. 외국화폐, 외국보조화폐, 외국지폐, 외국은행권, 외국유가증권 또는 그 밖의 외국채권5. 그 밖의 동산(動産) 및 선박[전문개정 2011. 9. 29.]
제1조(국내재산 도피 금지)누구든지 국내에 있는 재산을 도피시킬 목적으로 외국 또는 군사분계선 이북의 지역으로 재산을 이동하거나 이동하는 결과를 생기게 하는 행위를 할 수 없다.[전문개정 2010. 3. 31.]
제1조(형의 집행정지 통지 등)①검사는「형사소송법」제470조또는제471조에 따라 징역, 금고 또는 구류의 선고를 받은 자에 대하여 형의 집행을 정지한 때에는 다음 각 호의 사항을 형의 집행정지처분을 받은 자(이하 “형집행정지자”라 한다)의 거주지를 관할하는 경찰서장에게 통지하여야 한다.<개정 2012. 4. 23.>1. 등록기준지ㆍ주소ㆍ성명ㆍ연령 및 직업.2. 판결법원ㆍ판결 및 판결확정년월일.3. 죄명ㆍ형명 및 형기.4. 형의 집행정지처분을 한 연월일 및 형의 집행정지사유.5. 출소교도소명.6. 그 밖에 필요하다고 인정하는 사항.②형의 집행정지처분을 한 검사가 형집행정지자의 거주지를 관할하는 지방검찰청 또는 지청이 아닌 검찰청에 소속하는 경우에는 그 검사는 특별한 사유가 있는 경우를 제외하고는 집행정지에 관한 서류를 형집행정지자의 거주지를 관할하는 지방검찰청 또는 지청의 검사에게 송부하고, 그 송부를 받은 검사가 제1항의 규정에 의한 통지를 하여야 한다. <개정 1991ㆍ6ㆍ19>[제목개정 2012. 4. 23.]
국가보안유공자상금지급등에관한규정제8조단서의 규정에 의한 무기의 종류를 다음과 같이 정한다.1. 총포류2. 화약 기타 폭발물류
비영리법인의 업무를 집행하는 이사, 감사 또는 그 직무를 대행하는 사람이나 사원으로서 형사소추(刑事訴追) 또는 형의 

In [4]:
for item in documents:
    item['articles'].pop(0)

In [5]:
documents = documents + except_documents
print(len(documents))

156


In [15]:
from langchain_core.documents import Document

qdrant_datas = []
for item in documents:
    for i, article in enumerate(item['articles']):
        content = f'{item['title']} {article}'
        qdrant_datas.append(
            Document(
                page_content=content, 
                metadata={
                    'title': item['title'],
                    'url': item['url'],
                    'source': item['source'],
                    'seq': i + 1
                }
            )
        )
    

In [16]:

print(qdrant_datas)


[Document(metadata={'title': '특정범죄신고자등보호법시행령', 'url': 'https://www.law.go.kr/LSW/lsInfoP.do?lsiSeq=225685&ancYd=&ancNo=&efYd=20210101&nwJoYnInfo=Y&ancYnChk=0&efGubun=Y&vSct=*#0000', 'source': './datas/특정범죄신고자등보호법시행령.txt', 'seq': 1}, page_content='특정범죄신고자등보호법시행령 제2조(범죄신고자등보좌인의 자격)특정범죄신고자등보호법(이하 “법”이라 한다)제6조제2항에서 “대통령령이 정하는 자”라 함은 다음 각호의 1에 해당하는 자를 말한다.1. 학교ㆍ사회교육시설ㆍ사회복지시설 및 사회보호시설의 장 또는 그 직원2. 법률구조법등 법령에 규정된 상담소의 장 또는 그 직원3. 범죄신고자등의 고용주4. 기타 학식과 덕망이 있는 자로서 범죄신고자등을 위하여 충분한 조력을 할 수 있다고 인정되는 자'), Document(metadata={'title': '특정범죄신고자등보호법시행령', 'url': 'https://www.law.go.kr/LSW/lsInfoP.do?lsiSeq=225685&ancYd=&ancNo=&efYd=20210101&nwJoYnInfo=Y&ancYnChk=0&efGubun=Y&vSct=*#0000', 'source': './datas/특정범죄신고자등보호법시행령.txt', 'seq': 2}, page_content='특정범죄신고자등보호법시행령 제3조(보좌인에 대한 실비지급 등)①법제6조제10항의 규정에 의하여 범죄신고자등보좌인(이하 “보좌인”이라 한다)에게 지급할 수 있는 비용은 범죄신고자등과의 동행일수에 따른 일당ㆍ여비 및 숙박료(이하 이 조에서 “실비”라 한다)로 한다.②제1항의 규정에 의한 실비는 당해 사건의 진행경과에 따라 참고인 또는 증인에 준하여 지급하되, 수사단계에서는 수사기관이, 재판단계에서는 법원이 각각 이를 지급한다.'), Document(metada

In [3]:
from stores import init_vector_store, QDRANT_URL

vector_store = init_vector_store(documents)

/Users/tera/Desktop/workspace/skn_21/project/project_03_1team_repo/c_team/stores.py:19: UserWarning: Api key is used with an insecure connection.
  return QdrantClient(
/Users/tera/Desktop/workspace/skn_21/project/project_03_1team_repo/.venv/lib/python3.13/site-packages/langchain_qdrant/qdrant.py:921: UserWarning: Api key is used with an insecure connection.
  client = QdrantClient(**client_options)


In [6]:
from stores import get_client, COLLECTION_NAME
from qdrant_client.models import PayloadSchemaType

client = get_client()

client.create_payload_index(
    collection_name=COLLECTION_NAME,
    field_name="title",
    field_schema=PayloadSchemaType.TEXT,
)

/Users/tera/Desktop/workspace/skn_21/project/project_03_1team_repo/c_team/stores.py:19: UserWarning: Api key is used with an insecure connection.
  return QdrantClient(


UpdateResult(operation_id=105, status=<UpdateStatus.COMPLETED: 'completed'>)